In [1]:
# Import course structure and student video viewing features
import os, json, csv

courseStructure = []       
with open('/home/davidlemay/Downloads/TeachersCollegeX-BDE1x-2T2015-course_structure-prod-analytics.json', 'r') as f:
    courseStructure = json.load(f)

videoFeatures = []
with open('/home/davidlemay/Downloads/user-performance.csv', 'r') as f:
    reader = csv.reader(f)
    videoFeatures = list(reader)

In [10]:
print(chapters)

['block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@70778dec3400435b9e46363767bdfa86', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@22b0e3999f8e4d12a43b8b21bfa0eaa3', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@fe1d847c504849b090ddc9be0b35a2c7', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@474d7a5fab0c464890c5d05db65310ba', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@716f0331d4c74d11b25a3d8df6580698', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@e636b09aa0b6400ca68d1be197dceaa1', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@53cebfdd9a43484394ab6a5c7fda4525', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@5d4ba7155058487cb9be4f559186870a', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@610bb4cc820f478c9db9dbd4959a885d', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@24020ef534c34f4e8c59eaa800820eb1']


In [150]:
# Sort videos by chapter (because only chapters are associated with assignments), 
# requiring both ModuleID and YoutubeID because ModuleIDs weren't used in the feature extraction...
def getChapter(video): #takes list now (with moduleID = list[1]) but really should only take moduleID string and return moduleID for corresponding chapter...
    chapters = []
    moduleID = video[1]
    for item in courseStructure.items():
        if item[1]['category'] == 'course': 
            chapters = item[1]['children'] #get list of chapters
    for x in range(0,6): #depth of search
        for item in courseStructure.items(): 
            if moduleID in item[1]['children']:
                if moduleID in chapters:
                    continue
                else:
                    moduleID = item[0] #take parent element and repeat
                    #print(moduleID)
    return moduleID

sortedVideos = {}
videos = []
for item in courseStructure.items():
    #print(item[0], item[1]['category'])
    videoID = ''
    blockID = ''
    if item[1]['category'] == 'video': #get videoID and blockID
        videoID = item[1]['metadata'].get('youtube_id_1_0')
        blockID = item[0]
        videos.append((videoID, blockID))

#group verticals into sequentials into chapters (i.e., weeks) by iterating through courseStructure
for video in videos:
    chapter = getChapter(video)
    if chapter in sortedVideos.keys():
        sortedVideos[chapter].append((video))
    else:
        sortedVideos[chapter] = [video] #videos sorted by week
print(sortedVideos)

{'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@22b0e3999f8e4d12a43b8b21bfa0eaa3': [('RuFaWB3AQCs', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@video+block@0071232390e446028608c42eac2b2dfd'), ('aQmWf1YThFI', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@video+block@0997e5269fc64ac4b152ccdfdbb13cd1'), ('dc5Nx3tyR8g', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@video+block@1e314643491e463d893c602f35e148c7'), ('DC70-ugtFc8', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@video+block@24c6ac1e83f343b5b246bf9719fd24db'), ('QRVOW8W-xeI', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@video+block@2e04e822d0534830a00b09c281843fda'), ('O5rKkvLRXw4', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@video+block@3557768a4e1e485e8bf88def74eb1d41'), ('RHvxDieJlfE', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@video+block@52a4f4e6c131473b973630f40deed118'), ('TOmN4kfJrso', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@video+block@7609119b1eff427fae40386b59fb87e9'), ('k9Z4ibzH-1s', 'block-v1:Teache

In [70]:
print(videoFeatures[0])

['user', 'video', 'fracSpent', 'fracComp', 'fracPlay', 'numPauses', 'fracPaused', 'avgPBR', 'stdPBR', 'numRWs', 'numFFs']


In [83]:
# Match video with its chapter using sortedVideo dictionary
videoFeaturesByChapter = {}
for videoFeature in videoFeatures: #Iterate through video features
    videoID = videoFeature[1]
    for week in sortedVideos.items(): #Iterate through sorted videos
        for video in week[1]:
            if videoID in video:
                if week[0] in videoFeaturesByChapter.keys():
                    videoFeaturesByChapter[week[0]].append(videoFeature)
                else:
                    videoFeaturesByChapter[week[0]] = [videoFeature]

In [84]:
print(videoFeaturesByChapter['block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@610bb4cc820f478c9db9dbd4959a885d'])

[['1006805', 'saevAbGvRBM', '0.0', '0.0', '0.0', '0', '0.0', '0', '0', '0', '0'], ['4893040', 'YedABgZX5QM', '0.9993381275000001', '0.9988368950000001', '0.9988368950000001', '1', '0.61198172', '0', '0', '0', '0'], ['4893040', 'fbFp0uVOtng', '1.0020972173913043', '1.000835158695652', '1.000835158695652', '0', '0.0', '0', '0', '0', '0'], ['4893040', 'saevAbGvRBM', '1.0013376079295155', '1.0000997092511015', '1.0000997092511015', '0', '0.0', '0', '0', '0', '0'], ['4893040', 'I-f-SEfIntI', '1.0010757325581396', '1.0002240598006646', '1.0002240598006646', '1', '0.012224328903654486', '0', '0', '0', '0'], ['4893040', 'W6O7g-Ug_WE', '0.9994041877394636', '0.9971675287356321', '0.9971675287356321', '0', '0.0', '0', '0', '0', '0'], ['636013', 'YedABgZX5QM', '0.0', '0.0', '0.0', '0', '0.0', '0', '0', '0', '0'], ['636013', 'fbFp0uVOtng', '0.0', '0.0', '0.0', '0', '0.0', '0', '0', '0', '0'], ['636013', 'saevAbGvRBM', '0.0', '0.0', '0.0', '0', '0.0', '0', '0', '0', '0'], ['636013', 'I-f-SEfIntI', 

In [309]:
#Import studentGrades
studentGrades = []
with open('/home/davidlemay/Downloads/TeachersCollegeX-BDE1x-2T2015-courseware_studentmodule-prod-analytics.sql', 'r') as f:
    reader = csv.reader(f, delimiter='\t')
    firstRow = next(reader)
    print(firstRow)
    for row in reader:
        if row[1] == 'problem':
            studentGrades.append([row[3], row[2], row[5]])

['id', 'module_type', 'module_id', 'student_id', 'state', 'grade', 'created', 'modified', 'max_grade', 'done', 'course_id']


In [310]:
sortedGrades = {}
chapters = []
for item in courseStructure.items():
    if item[1]['category'] == 'course': 
        chapters = item[1]['children'] #get list of chapters
#print(len(studentGrades))
#print(chapters)
for grade in studentGrades:
    moduleID = grade[1]
    for x in range(0,6):
        for item in courseStructure.items():
            if moduleID in chapters:
                continue
            if moduleID in item[1]['children']:
                moduleID = item[0]
    #print(chapter)
    if moduleID in sortedGrades.keys():
        sortedGrades[moduleID].append(grade)
    else:
        sortedGrades[moduleID] = [grade]

In [312]:
print(sortedGrades['block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@22b0e3999f8e4d12a43b8b21bfa0eaa3'])

[['7536436', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@93bd02b0d9e942b586a396a63dfe2b03', 'NULL'], ['7536436', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@2f657952c27a40608458db76900245b5', 'NULL'], ['7536436', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@b919d1519c7d48798f8d6e27aece6c9f', 'NULL'], ['7536436', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@8cdb97f23a7a449b991b81ee5e4be4fb', 'NULL'], ['7739677', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@8f5577b67cc54afe9e589836a179202c', 'NULL'], ['4764625', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@8f5577b67cc54afe9e589836a179202c', 'NULL'], ['1969714', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@8f5577b67cc54afe9e589836a179202c', '0'], ['1317032', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@8f5577b67cc54afe9e589836a179202c', '0'], ['7566022', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@lti+block@224f241077594ef890

In [238]:
# Test: Get chapter for assignment grade and sort grades by chapter
sortedGrades = {}
testGrades = studentGrades
for testGrade in testGrades:
    moduleID = testGrade[1]
    level = 1
    isChapter = False
    for x in range(0,6):
        for item in courseStructure.items():
            if moduleID in chapters:
                isChapter = True
                continue
            if moduleID in item[1]['children']:
                moduleID = item[0]
                level += 1
                #print(moduleID, level)
    if moduleID in sortedGrades.keys():
        sortedGrades[moduleID].append(testGrade)
    else:
        sortedGrades[moduleID] = [testGrade]
#print(sortedGrades.keys())
#print(json.dumps(sortedGrades, indent=4, sort_keys=True))

In [313]:
print(sortedGrades.keys())

dict_keys(['block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@22b0e3999f8e4d12a43b8b21bfa0eaa3', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@716f0331d4c74d11b25a3d8df6580698', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@474d7a5fab0c464890c5d05db65310ba', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@fe1d847c504849b090ddc9be0b35a2c7', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@53cebfdd9a43484394ab6a5c7fda4525', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@5d4ba7155058487cb9be4f559186870a', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@610bb4cc820f478c9db9dbd4959a885d', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@e636b09aa0b6400ca68d1be197dceaa1', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@aaf5ea5718c14d288ac4a4e74652110b', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@a2884d9e196c490881dd030363f34711', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@prob

In [275]:
#Group videoFeaturesByChapter for each studentID
videosByWeekByStudent = {}
for item in videoFeaturesByChapter.items():
    videoList = item[1]
    videosByStudent = {}
    for video in videoList:
        studentID = video[0]
        if studentID in videosByStudent.keys(): 
            videosByStudent[studentID].append(video)
        else:
            videosByStudent[studentID] = [video]
    videosByWeekByStudent[item[0]] = videosByStudent
print(len(videosByWeekByStudent))

9


In [314]:
print(videosByWeekByStudent['block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@22b0e3999f8e4d12a43b8b21bfa0eaa3']['7583992'])

[['7583992', 'dc5Nx3tyR8g', '1.0016362307692306', '1.0008677884615385', '1.0008677884615385', '1', '0.2656064375', '0', '0', '0', '0'], ['7583992', 'DC70-ugtFc8', '1.1860456458715596', '0.9991229357798164', '1.1815467889908255', '2', '0.3018605504587156', '0', '0', '0', '4'], ['7583992', 'RHvxDieJlfE', '1.008697', '0.9994722222222223', '0.9994722222222223', '0', '0.0', '0', '0', '0', '0'], ['7583992', 'TOmN4kfJrso', '1.003571815705128', '1.0004198717948718', '1.0004198717948718', '2', '0.09141517467948719', '0', '0', '0', '0'], ['7583992', 'k9Z4ibzH-1s', '0.975909429245283', '0.9742783018867924', '0.9742783018867924', '0', '0.0', '0', '0', '0', '0'], ['7583992', '8X0UlMShss4', '1.0048255575757576', '0.9980686868686869', '0.9980686868686869', '5', '0.16745479393939391', '0', '0', '0', '0']]


In [324]:
#Combine individual student video features for each week
studentWeekPerformance = {}
for week in videosByWeekByStudent.items(): #Get full video list for week
    videoLists = week[1]
    for student in videoLists.items(): #Get student video list for week
        videoFeatures = student[1]
        user = videoFeatures[0][0]
        numVids = len(videoFeatures)
        sumFracSpent = sumFracComp = sumFracPlay = sumNumPauses = sumFracPaused = sumAvgPBR = sumAvgStdPBR = sumNumRWs = sumNumFFs = avgFracSpent = avgFracComp = avgFracPlay = avgFracPaused = avgPBR = stdPBR = 0
        for videoFeature in videoFeatures: #Sum video features for student
            sumFracSpent += float(videoFeature[2])
            sumFracComp += float(videoFeature[3])
            sumFracPlay += float(videoFeature[4])
            sumNumPauses += int(videoFeature[5])
            sumFracPaused += float(videoFeature[6])
            sumAvgPBR += float(videoFeature[7])
            sumAvgStdPBR += float(videoFeature[8])
            sumNumRWs += int(videoFeature[9])
            sumNumFFs += int(videoFeature[10])
            avgFracSpent = sumFracSpent/numVids
            avgFracComp = sumFracComp/numVids
            avgFracPlay = sumFracPlay/numVids
            avgFracPaused = sumFracPaused/numVids
            avgPBR = sumAvgPBR/numVids
            stdPBR = sumAvgStdPBR/numVids
        if week[0] in studentWeekPerformance.keys():
            studentWeekPerformance[week[0]].append([user, numVids, avgFracSpent, avgFracComp, avgFracPlay, sumNumPauses, avgFracPaused, avgPBR, stdPBR, sumNumRWs, sumNumFFs])
        else:
            studentWeekPerformance[week[0]] = [[user, numVids, avgFracSpent, avgFracComp, avgFracPlay, sumNumPauses, avgFracPaused, avgPBR, stdPBR, sumNumRWs, sumNumFFs]]
print(studentWeekPerformance['block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@70778dec3400435b9e46363767bdfa86'])
            

[['8305451', 1, 0.014479423011844333, 0.013174280879864603, 0.013174280879864603, 0, 0.0, 0.0, 0.0, 0, 4], ['4691550', 4, 0.11141708798646362, 0.11115348561759729, 0.11115348561759729, 1, 0.010364862732656514, 0.0, 0.0, 0, 0], ['6964414', 1, 0.00918987394247039, 0.01032765651438237, 0.014919193739424672, 1, 0.003120311336717428, 1.25, 0.0, 3, 0], ['634646', 2, 0.9683750813325874, 0.4760499843459278, 0.5614979737706318, 5, 1.007958069757445, 0.0, 0.0, 3, 0], ['2073967', 2, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0], ['4733169', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0], ['7458297', 1, 0.043502871404399325, 0.04325490778341794, 0.04325490778341794, 0, 0.0, 0.0, 0.0, 0, 0], ['6648513', 4, 0.15307437394247042, 0.042993458394471766, 0.042993458394471766, 9, 0.06187253384094755, 0.0, 0.0, 0, 0], ['6877908', 1, 0.032475439932318106, 0.0383248730964467, 0.0383248730964467, 0, 0.0, 0.0, 0.0, 0, 0], ['4302082', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0], ['7222977', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0

In [325]:
# Match grade with videosByWeekByStudent
for week in sortedGrades.items():
    gradesList = week[1]
    weekID = week[0]
    for chapter in studentWeekPerformance.items():
        videosList = chapter[1]
        chapterID = chapter[0]
        weekVideosGrades = {}
        if weekID == chapterID:
            for grade in gradesList:                
                gradeStudentID = grade[0]
                gradeScore = grade[2]
                if gradeStudentID not in weekVideosGrades.keys(): #Only add once                  
    #                print(gradeStudentID, gradeScore)
                    for video in videosList:
                        videoStudentID = video[0]
    #                    print(video)
                        if gradeStudentID == videoStudentID: #Only one video feature and one grade for each student per week. 
                            weekVideosGrades[gradeStudentID] = video
                            weekVideosGrades[gradeStudentID].append(gradeScore)
                            print(weekVideosGrades[gradeStudentID])
    #                        with open('/home/davidlemay/Downloads/user-weekly-performance.csv', 'a') as f:
    #                            writer = csv.writer(f)
    #                            writer.writerow(weekVideosGrades[gradeStudentID])

['7536436', 2, 0.5032393810096154, 0.5010501634615385, 0.5010501634615385, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['7739677', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['4764625', 2, 1.3275308143485212, 0.995201648281375, 1.0532202130295762, 4, 0.14237304866107114, 0.875, 0.11458333333333333, 1, 1, 'NULL']
['1969714', 2, 0.4647516249999999, 0.4494531249999999, 0.45056009615384607, 5, 0.11669169711538463, 0.0, 0.0, 2, 6, '0']
['1317032', 3, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, '0']
['7566022', 6, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, '0.307692307']
['1831358', 2, 0.0815937256880734, 0.08016513761467889, 0.08016513761467889, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['7739958', 2, 0.5047284861111111, 0.5005694444444444, 0.5005694444444444, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['4517805', 2, 1.9697874342525978, 0.6659581573741007, 0.6659581573741007, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['4642224', 6, 0.2504556495965338, 0.31171313553318625, 0.3117131355331862, 8, 0.2476100141395816, 0.0, 0.0, 0, 0, '0']

['7719039', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['335489', 6, 1.3114879942221378, 0.9988085869958786, 0.9988085869958786, 2, 0.17394408144090234, 0.0, 0.0, 0, 0, '1']
['1741246', 6, 1.0116048714098302, 0.8317493652144125, 0.9773091265565123, 27, 0.42458523308743074, 0.0, 0.0, 29, 0, '1']
['3251135', 2, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['7589696', 2, 0.51980475, 0.5024540138888889, 0.5024540138888889, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['1920285', 5, 0.5711920186233558, 0.4914071504895722, 0.4914071504895722, 14, 0.7872227142105668, 0.0, 0.0, 0, 0, 'NULL']
['951411', 6, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, '1']
['6255450', 4, 0.5535827696093358, 0.5423703760492874, 0.5507726844852766, 13, 0.2035782261840652, 0.25, 0.0, 15, 5, '1']
['2022117', 6, 0.009784031804281347, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, '1']
['7765545', 2, 0.1302421527777778, 0.12470833333333332, 0.12470833333333332, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['6774419', 6, 0.9746561264274846, 0.90400350949

['6474711', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['384401', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['620356', 3, 0.47545809539267664, 0.4684988805286046, 0.4684988805286046, 3, 5.433556560018651, 0.0, 0.0, 0, 0, 'NULL']
['2261552', 2, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['4622279', 2, 0.7625403153206598, 0.7590842583719578, 0.7590842583719578, 2, 0.5638044735576924, 0.0, 0.0, 0, 0, 'NULL']
['1087969', 5, 0.26208634526829244, 0.5714913660718264, 0.5714913660718264, 0, 0.0, 0.0, 0.0, 0, 24, 'NULL']
['7250101', 6, 0.233155898867922, 0.33707616874983654, 0.33707616874983654, 1, 0.00016372248427672955, 0.0, 0.0, 0, 23, '1']
['7368348', 6, 0.46017186589464126, 0.4487708090806721, 0.45481706593182514, 5, 0.07360269652805454, 0.0, 0.0, 2, 0, '1']
['4862710', 4, 0.8071584381595779, 0.7961389466929157, 0.7961389466929157, 7, 0.3302748910022804, 0.0, 0.0, 0, 0, 'NULL']
['7058447', 5, 0.00020072106918238996, 0.0, 0.0, 1, 0.023706404716981135, 0.0, 0.0, 0, 0, 'NUL

['163026', 6, 0.4075306942591568, 0.6643769602752337, 0.6832179368884571, 10, 0.5091186084200776, 0.25, 0.0, 3, 0, '1']
['4518430', 4, 8.169960468401062, 0.499794938568376, 0.499794938568376, 8, 0.2927634747596154, 0.0, 0.0, 0, 0, 'NULL']
['1272021', 5, 0.5049837434217486, 0.7474973964505058, 0.7474973964505058, 6, 0.0320408965165759, 0.0, 0.0, 0, 0, '1']
['5743275', 2, 0.8867644766187049, 0.49905632254196636, 0.49905632254196636, 2, 0.09445192925659472, 0.0, 0.0, 0, 0, 'NULL']
['2513250', 4, 0.7889066324661302, 0.711470809017043, 0.7424731291626765, 45, 1.1440333470262356, 0.0, 0.0, 7, 1, '1']
['7489578', 2, 1.006874009292566, 0.999769284572342, 0.999769284572342, 2, 0.16033309232613907, 0.0, 0.0, 0, 0, 'NULL']
['3661128', 6, 0.1675831983173077, 0.16698717948717948, 0.16698717948717948, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['7118468', 5, 0.4262288241634165, 0.6289794915075113, 0.6289794915075113, 2, 0.02808383940110092, 0.3, 0.0, 0, 0, '1']
['1876184', 2, 0.13293504166666667, 0.126581, 0.1

['7473778', 3, 0.20023325721153842, 0.19698397435897433, 0.19698397435897433, 1, 11.421736384615386, 0.0, 0.0, 1, 0, 'NULL']
['7367289', 2, 0.6086147462030376, 0.5435081366906475, 0.5435081366906475, 2, 0.10442883802957634, 0.0, 0.0, 3, 0, 'NULL']
['7395333', 2, 1.002612179656275, 0.998839928057554, 0.998839928057554, 1, 0.9621025694444444, 0.0, 0.0, 0, 0, 'NULL']
['4206133', 5, 0.5896437255465736, 0.6108849584653522, 0.6768930195764634, 5, 0.22174178244648318, 0.75, 0.0125, 0, 0, '1']
['3340260', 2, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['595145', 2, 0.5034914166666666, 0.5004112638888889, 0.5004112638888889, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['6542564', 2, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['7542295', 3, 0.335703462962963, 0.3345113240740741, 0.3345113240740741, 1, 0.45762238060897437, 0.0, 0.0, 0, 0, 'NULL']
['7423204', 2, 0.5003632757793766, 0.03047235611510793, 0.03047235611510793, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['5118871', 6, 0.3974924512491343, 0.39717233416

...

['4240833', 4, 0.2514856550480769, 0.25048420979426456, 0.25048420979426456, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['5099361', 5, 0.0033957555645730414, 0.003290549654375441, 0.003290549654375441, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['1838727', 6, 0.00011206834532374101, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['882647', 4, 0.0026384419191919192, 0.0023535353535353537, 0.0023535353535353537, 1, 0.5268974565656566, 0.375, 0.0625, 0, 0, 'NULL']
['3303607', 3, 0.5387344825266603, 0.6631155636990642, 0.6631155636990642, 8, 1.7361472412543455, 0.0, 0.0, 0, 0, 'NULL']
['3521509', 3, 0.6178722608579803, 0.594455102584599, 0.6164391153743671, 1, 0.41443019744204634, 0.0, 0.0, 1, 1, 'NULL']
['7181517', 2, 0.09526466586538461, 0.09409014423076924, 0.09442788461538462, 0, 0.0, 0.0, 0.0, 1, 0, 'NULL']
['6876592', 4, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['6156379', 6, 0.20564365513710828, 0.20523739285078346, 0.20523739285078346, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['8069158', 2, 0.608360528177458, 0

['8286606', 2, 0.28191220793269234, 0.3375783920940171, 0.3375783920940171, 2, 0.6432627777777777, 1.375, 0.03125, 0, 3, 'NULL']
['1026680', 1, 1.0000395, 0.9921302777777777, 0.9921302777777777, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['3767990', 5, 0.5000999262417578, 0.43941650394964105, 0.43941650394964105, 1, 0.0015583528846153847, 0.0, 0.0, 0, 1, 'NULL']
['8372377', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['7584280', 2, 0.8478932362446581, 0.8413695032051283, 0.8413695032051283, 2, 0.12890606610576924, 0.0, 0.0, 0, 0, 'NULL']
['1887801', 3, 0.3360132777777778, 0.3332962962962963, 0.3332962962962963, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['1584099', 2, 1.0055443836805555, 1.0023122246260683, 1.0023122246260683, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['8344329', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['96314', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['6096155', 1, 0.20667138461538462, 0.20533172596153845, 0.20533172596153845, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['8328577', 2, 

['7732691', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['2800189', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['7733033', 1, 0.2842917243902439, 0.2823879024390244, 0.2823879024390244, 0, 0.0, 0.0, 0.0, 0, 1, 'NULL']
['2506846', 9, 1.4020864319405533, 0.9992985711639452, 1.3891029207706782, 32, 40.709994770630175, 0.0, 0.0, 10, 1, 'NULL']
['2508834', 9, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['614566', 2, 0.5010907792682927, 0.4994455280487805, 0.4994455280487805, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['728088', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['6748246', 5, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['5416177', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['2802883', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['1211668', 3, 0.03885016419619128, 0.16919695819062444, 0.16919695819062444, 0, 0.0, 0.0, 0.0, 2, 10, '0.272727272']
['7692435', 3, 0.6008888229403532, 0.5862492641222815, 0.5993434072557438, 1, 3.2955347182462926, 0.0, 0.0, 1, 0

['7303495', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['7503596', 5, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, '0']
['2042157', 5, 1.0143121197271605, 0.7584843354547446, 1.0023462310060018, 13, 1.5747320626692456, 0.0, 0.0, 5, 0, '0']
['4045599', 5, 0.4429069014124639, 0.39972942491862057, 0.5056888059631082, 6, 1.1455240175590886, 0.0, 0.0, 9, 12, '1']
['6770267', 1, 0.05258926097560975, 0.04859761463414629, 0.04859761463414629, 1, 0.04304914146341464, 0.0, 0.0, 0, 1, 'NULL']
['5525267', 8, 0.6508496041391619, 0.6469631450265586, 0.6469631450265586, 8, 2.999992303472881, 0.0, 0.0, 3, 4, '0']
['3186434', 2, 0.17087429390243905, 0.16648780487804873, 0.16823170731707315, 0, 0.0, 0.0, 0.0, 2, 5, 'NULL']
['4106339', 4, 1.076012969482183, 0.9934243107844067, 1.069940883090645, 40, 14.599014018024015, 0.0, 0.0, 1, 1, '0.25']
['4758275', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['1727293', 9, 0.17152392543839426, 0.15160100101946203, 0.15160100101946203, 1, 0.04422176202478471,

['1035036', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, '0']
['7534688', 2, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['4977775', 5, 1.3328993010369392, 0.3992526991385573, 0.7020456934198235, 46, 0.6642896665924424, 0.0, 0.0, 5, 1, '1']
['2932511', 9, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, '1']
['7375883', 2, 0.9043478637650422, 0.6678931168656923, 0.8981688632071557, 2, 0.32809886097560975, 0.0, 0.0, 0, 2, 'NULL']
['3764297', 5, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['316203', 5, 1.5383309865173085, 0.8000351250271167, 1.4451472019595522, 16, 4.516949335302977, 0.0, 0.0, 23, 2, 'NULL']
['4354374', 3, 0.4503475127086017, 0.5167287615075834, 0.5167287615075834, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['5803635', 9, 0.11177757235772358, 0.1110125382113821, 0.1110125382113821, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['8188649', 1, 0.0, 0.0, 0.0, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['8059301', 1, 0.9999249414634146, 1.0000447024390244, 1.0000447024390244, 0, 0.0, 0.0, 0.0, 0, 0, 'NULL']
['4690534

In [284]:
print(sortedGrades['block-v1:TeachersCollegeX+BDE1x+2T2015+type@chapter+block@22b0e3999f8e4d12a43b8b21bfa0eaa3'])

[('7536436', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@93bd02b0d9e942b586a396a63dfe2b03', 'NULL'), ('7536436', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@2f657952c27a40608458db76900245b5', 'NULL'), ('7536436', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@b919d1519c7d48798f8d6e27aece6c9f', 'NULL'), ('7536436', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@8cdb97f23a7a449b991b81ee5e4be4fb', 'NULL'), ('7739677', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@8f5577b67cc54afe9e589836a179202c', 'NULL'), ('4764625', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@8f5577b67cc54afe9e589836a179202c', 'NULL'), ('1969714', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@8f5577b67cc54afe9e589836a179202c', '0'), ('1317032', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@problem+block@8f5577b67cc54afe9e589836a179202c', '0'), ('7566022', 'block-v1:TeachersCollegeX+BDE1x+2T2015+type@lti+block@224f241077594ef890